In [4]:
!pip install spotipy --upgrade

import numpy as np
import pandas as pd
import os
import requests

import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
from difflib import SequenceMatcher


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip


In [ ]:
SPOTIFY_CLIENT_ID = 'key'
SPOTIFY_CLIENT_SECRET = 'key'

auth_manager = SpotifyClientCredentials(SPOTIFY_CLIENT_ID, SPOTIFY_CLIENT_SECRET)
request_limit = 2480

spotify = spotipy.Spotify(auth_manager=auth_manager)

results = spotify.search(q='%20track:behind the crooked cross%20artist:slayer%20', type='track,album', limit=10)
print(results['tracks'])
print(results['albums'])

# for artist in results["artists"]["items"]:
#   print(artist)
#   print(artist['name'])
#   print(artist["genres"])
#   print(artist["external_urls"])
# # items = results['artists']['items']
# # if len(items) > 0:
# #     artist = items[0]
# #     print(artist['name'], artist['images'][0]['url'])

{'href': 'https://api.spotify.com/v1/search?offset=0&limit=10&query=%2520track%3Abehind%20the%20crooked%20cross%2520artist%3Aslayer%2520&type=track', 'limit': 10, 'next': 'https://api.spotify.com/v1/search?offset=10&limit=10&query=%2520track%3Abehind%20the%20crooked%20cross%2520artist%3Aslayer%2520&type=track', 'offset': 0, 'previous': None, 'total': 1000, 'items': [{'album': {'album_type': 'single', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/0TO6y1x0LQodwBnxGtQu9o'}, 'href': 'https://api.spotify.com/v1/artists/0TO6y1x0LQodwBnxGtQu9o', 'id': '0TO6y1x0LQodwBnxGtQu9o', 'name': 'shadowraze', 'type': 'artist', 'uri': 'spotify:artist:0TO6y1x0LQodwBnxGtQu9o'}, {'external_urls': {'spotify': 'https://open.spotify.com/artist/3AqIMsKWh90Y41un7hL29x'}, 'href': 'https://api.spotify.com/v1/artists/3AqIMsKWh90Y41un7hL29x', 'id': '3AqIMsKWh90Y41un7hL29x', 'name': 'GENJUTSU', 'type': 'artist', 'uri': 'spotify:artist:3AqIMsKWh90Y41un7hL29x'}], 'available_markets': ['AR',

In [6]:
all_songs = pd.read_csv('./tcc_ceds_music_full.csv')

In [ ]:
start_idx=21200 #pop
artist_permissible_similarity = 0.95
track_permissible_similarity = 0.85
#country = 7042
#blues = 12487
#jazz = 17091
#reggae = 20936
#rock = 23434
#hip-hop = 27468

In [16]:
for idx,(artist,track,year) in enumerate(zip(all_songs["artist_name"][start_idx:],all_songs["track_name"][start_idx:],all_songs["release_date"][start_idx:])):
  artist = artist.strip().lower()
  track = track.strip().lower()

  print(f"Artist: {artist}; Track: {track}")
  
  request_succeeded = False
  while not request_succeeded:
    try:
      search_result = spotify.search(q=f'%20track:{track}%20artist:{artist}%20year:{year-3}-{year+3}%20', type='track', limit=50)
      request_succeeded = True
    except:
      pass

  if search_result['tracks']['total'] == 0:
    print("No matching items found")
    continue

  cover_url = ''

  #tries to match artist and track by name exactly
  # for search_item in search_result['tracks']['items']:
  #   examined_artist_name = search_item['artists'][0]['name'].strip().lower()
  #   examined_track_name = search_item['name'].strip().lower()

  #   print(f"Examined artist: {examined_artist_name}")

  #   artists_not_same = SequenceMatcher(None, examined_artist_name, artist).ratio() < artist_permissible_similarity and SequenceMatcher(None,artist, examined_artist_name).ratio() < artist_permissible_similarity
  #   tracks_not_same = SequenceMatcher(None, examined_track_name, track).ratio() < track_permissible_similarity and SequenceMatcher(None, track, examined_track_name).ratio() < track_permissible_similarity
    
  #   if artists_not_same or tracks_not_same:
  #     continue

  #   album_item = search_item['album']
  #   if len(album_item['images']) > 0:
  #     cover_url = album_item['images'][0]['url']
  #     print("[]=> Found ~perfect~ match")
  #     break

  #tries to match artist by name exactly
  # if cover_url == '':
  #   for search_item in search_result['tracks']['items']:
  #     examined_artist_name = search_item['artists'][0]['name'].strip().lower()

  #     artists_not_same = SequenceMatcher(None, examined_artist_name, artist).ratio() < artist_permissible_similarity and SequenceMatcher(None,artist, examined_artist_name).ratio() < artist_permissible_similarity
      
  #     if artists_not_same:
  #       continue

  #     album_item = search_item['album']
  #     if len(album_item['images']) > 0:
  #       cover_url = album_item['images'][0]['url']
  #       print("[]=> Found match by artist")
  #       break

  #picks the most matching cover
  # if cover_url == '':
  #   for search_item in search_result['tracks']['items']:
  #     album_item = search_item['album']
  #     if len(album_item['images']) > 0:
  #       cover_url = album_item['images'][0]['url']
  #       print("[]=> Picked the first available cover")
  #       break

  #picks the best matching response
  max_artist_match_ratio = 0
  max_track_match_ratio = 0
  artist_diff_epsilon = 0.05

  for search_item in search_result['tracks']['items']:
    examined_artist_name = search_item['artists'][0]['name'].strip().lower()
    examined_track_name = search_item['name'].strip().lower()

    print(f"Examined artist: {examined_artist_name}; Examined track: {examined_track_name}")
    
    artist_match_ratio = np.max([SequenceMatcher(None, examined_artist_name, artist).ratio(), SequenceMatcher(None, artist, examined_artist_name).ratio() ])
    track_match_ratio = np.max([SequenceMatcher(None, examined_track_name, track).ratio(), SequenceMatcher(None, track, examined_track_name).ratio() ])

    update_cover_url = False
    if artist_match_ratio > max_artist_match_ratio:
      max_artist_match_ratio = artist_match_ratio
      update_cover_url = True
    
    if abs(artist_match_ratio - max_artist_match_ratio) <= artist_diff_epsilon and track_match_ratio > max_track_match_ratio:
      max_artist_match_ratio = np.max([artist_match_ratio, max_artist_match_ratio])
      max_track_match_ratio = track_match_ratio
      update_cover_url = True

    if update_cover_url:
      album_item = search_item['album']
      if len(album_item['images']) > 0:
        cover_url = album_item['images'][0]['url']

  if cover_url == '':
    print(f"No suitable cover found for idx {idx+start_idx}")
    continue
  
  print(f"Eventual URL for idx {idx+start_idx}: {cover_url}")
  print(f"Best artist match: {max_artist_match_ratio}; Best track match: {max_track_match_ratio}")
  downloaded_cover = requests.get(cover_url)

  # Save the image to the specified path
  with open(f"./retrieved_covers/{idx+start_idx}__{artist.replace('/','_')}__{track.replace('/','_')}__.jpeg", "wb") as f:
      f.write(downloaded_cover.content)







Artist: cynic; Track: the space for this
Examined artist: улица восток; Examined track: декаданс
Examined artist: без обмежень; Examined track: 24/02
Examined artist: the last passenger; Examined track: тунельний робітник
Examined artist: azzi; Examined track: мне не 20
Examined artist: не панк; Examined track: 20 или 5
Examined artist: space of variations; Examined track: tibet
Examined artist: созвездие скейтов; Examined track: 20!
Examined artist: sasha boole; Examined track: too old to sell my soul
Examined artist: yuvi; Examined track: цьом
Examined artist: the hardkiss; Examined track: hammer
Examined artist: the hardkiss; Examined track: shadows of time
Examined artist: motanka; Examined track: pace of the space
Examined artist: the hardkiss; Examined track: shadows of light
Examined artist: yuri kane; Examined track: right back (mixed)
Examined artist: монтеск'є; Examined track: паліатив
Examined artist: space of variations; Examined track: tribe
Examined artist: був'є; Examine

ConnectionError: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))